In [1]:
!pip install wandb

In [2]:
!pip install rouge-score

In [5]:
import nltk
nltk.download('wordnet')
nltk.download('omw-1.4')  # Optional: Download WordNet's extended multilingual data

[nltk_data] Downloading package wordnet to /usr/share/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /usr/share/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


True

In [3]:
!pip install --upgrade nltk

In [ ]:
!pip uninstall preprocessing -y

In [4]:
import nltk
print(nltk.__version__)

3.9.1


In [6]:
!pip install sentence_transformers

In [7]:
import torch
from transformers import BartTokenizer, BartForConditionalGeneration, AdamW, get_linear_schedule_with_warmup
from tqdm import tqdm
import pandas as pd
from sklearn.model_selection import train_test_split
from torch.utils.data import Dataset, DataLoader
import numpy as np
import math
import wandb
from rouge_score import rouge_scorer
# from dotenv import load_dotenv
import os
from tabulate import tabulate
from nltk.translate.bleu_score import corpus_bleu
from nltk.translate.meteor_score import meteor_score
import sympy as sp
# load_dotenv()
from sklearn.metrics.pairwise import cosine_similarity
from nltk.translate.meteor_score import meteor_score
from sentence_transformers import SentenceTransformer
from sklearn.metrics import accuracy_score
from fuzzywuzzy import fuzz

/opt/conda/lib/python3.10/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [8]:
df = pd.read_csv('/kaggle/input/final-cleaned-data/cleaned_final_data - cleaned_final_data.csv')

# If 'Unnamed: 0' column still exists, you can drop it
df = df.loc[:, ~df.columns.str.contains('^Unnamed')]

# 80% -> Training Data, 20% -> Testing Data
train_df, test_df = train_test_split(df, test_size=0.2, random_state=42)

# 90% -> Training Data, 10% -> Validation Data
train_df, val_df = train_test_split(train_df, test_size=0.1, random_state=42)

In [9]:
df.shape

(8988, 3)

In [10]:
tokenizer = BartTokenizer.from_pretrained('facebook/bart-base')

def calculate_max_length(column_name):
    df[column_name] = df[column_name].astype(str)
    return df[column_name].apply(lambda x: len(tokenizer.tokenize(x))).max()

max_length_question = calculate_max_length('Question')
max_length_object = calculate_max_length('Object')
max_length_answer = calculate_max_length('Answer')
# max_length_context = calculate_max_length('Context')

print(f"Maximum token length in the 'Question' column: {max_length_question + max_length_object}")
print(f"Maximum token length in the 'Answer' column: {max_length_answer}")

Maximum token length in the 'Question' column: 39
Maximum token length in the 'Answer' column: 62


In [11]:
model = BartForConditionalGeneration.from_pretrained('facebook/bart-base')

In [12]:
class Dataset(Dataset):
    '''For Loading the datasetS! '''
    def __init__(self, data, question_max_length=50, answer_max_length=75):
        self.data = data
        self.tokenizer = tokenizer
        self.question_max_length = question_max_length
        self.answer_max_length = answer_max_length

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        question = self.data.iloc[idx, 0]
        object_name = self.data.iloc[idx, 1]
        answer = self.data.iloc[idx, 2]
        # context = self.data.iloc[idx, 3]
        combined = str(object_name) + ' ' + str(question) 

        inputs = self.tokenizer(
            combined,
            max_length=self.question_max_length,
            padding='max_length',
            truncation=True,
            return_tensors="pt"
        )

        targets = self.tokenizer(
            answer,
            max_length=self.answer_max_length,
            padding='max_length',
            truncation=True,
            return_tensors="pt"
        )

        input_ids = inputs.input_ids.squeeze()
        attention_mask = inputs.attention_mask.squeeze()
        target_ids = targets.input_ids.squeeze()

        return {

            'input_ids': input_ids,
            'attention_mask': attention_mask,
            'labels': target_ids
        }

In [13]:
model

BartForConditionalGeneration(
  (model): BartModel(
    (shared): BartScaledWordEmbedding(50265, 768, padding_idx=1)
    (encoder): BartEncoder(
      (embed_tokens): BartScaledWordEmbedding(50265, 768, padding_idx=1)
      (embed_positions): BartLearnedPositionalEmbedding(1026, 768)
      (layers): ModuleList(
        (0-5): 6 x BartEncoderLayer(
          (self_attn): BartSdpaAttention(
            (k_proj): Linear(in_features=768, out_features=768, bias=True)
            (v_proj): Linear(in_features=768, out_features=768, bias=True)
            (q_proj): Linear(in_features=768, out_features=768, bias=True)
            (out_proj): Linear(in_features=768, out_features=768, bias=True)
          )
          (self_attn_layer_norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
          (activation_fn): GELUActivation()
          (fc1): Linear(in_features=768, out_features=3072, bias=True)
          (fc2): Linear(in_features=3072, out_features=768, bias=True)
          (final_lay

In [14]:
train_dataset = Dataset(train_df)
val_dataset = Dataset(val_df)
test_dataset = Dataset(test_df)

In [15]:
class VQA_Trainer:
    '''Class for Trainer Setup to Train the BART Model for VQA'''

    def __init__(self, model, train_dataloader, eval_dataloader, device, config):
        ''' Constructor '''
        self.model = model
        self.train_dataloader = train_dataloader
        self.eval_dataloader = eval_dataloader
        self.device = device
        self.tokenizer = BartTokenizer.from_pretrained('facebook/bart-base')
        self.scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)  # Initialize ROUGE scorer

        # Semantic similarity model
        self.semantic_model = SentenceTransformer('all-MiniLM-L6-v2')  # Pretrained sentence embedding model

        self.optimizer = AdamW(self.model.parameters(), lr=config['learning_rate'], weight_decay=config['weight_decay'])
        self.scheduler = get_linear_schedule_with_warmup(self.optimizer, num_warmup_steps=config['warmup_steps'], num_training_steps=len(self.train_dataloader) * config['epochs'])

        self.model.config.dropout = config['dropout']
        self.model.config.attention_dropout = config['attention_dropout']
        self.num_beams = config['num_beams']

        wandb.init(project=config['project_name'], config=config)
        wandb.watch(self.model, log="all")

    def evaluate(self):
        ''' For Evaluation at the End of Each Epoch '''
        self.model.eval()
        total_loss = 0
        predictions = []
        references = []
        token_level_accuracies = []
        exact_match_accuracies = []
        fuzzy_match_accuracies = []  # Add fuzzy match accuracy list
        semantic_similarities = []
        meteor_scores = []

        progress_bar = tqdm(self.eval_dataloader, desc="Evaluating")

        for batch in progress_bar:
            with torch.no_grad():
                inputs = {key: val.to(self.device) for key, val in batch.items()}
                outputs = self.model(**inputs)
                total_loss += outputs.loss.item()

                summary_ids = self.model.generate(inputs['input_ids'], max_length=80, num_beams=self.num_beams, early_stopping=True)
                decoded_preds = self.tokenizer.batch_decode(summary_ids, skip_special_tokens=True)

                labels = batch['labels']
                labels = torch.where(labels != -100, labels, self.tokenizer.pad_token_id)
                decoded_refs = self.tokenizer.batch_decode(labels, skip_special_tokens=True)

                predictions.extend([pred.split() for pred in decoded_preds])
                references.extend([[ref.split()] for ref in decoded_refs])

                for pred, ref in zip(decoded_preds, decoded_refs):
                    pred_tokens = pred.split()
                    ref_tokens = ref.split()

                    # Token-level accuracy
                    token_accuracy = sum(1 for p, r in zip(pred_tokens, ref_tokens) if p == r) / max(len(ref_tokens), 1)
                    token_level_accuracies.append(token_accuracy)

                    # Exact Match Accuracy
                    exact_match_accuracy = 1 if pred.strip() == ref.strip() else 0
                    exact_match_accuracies.append(exact_match_accuracy)

                    # Fuzzy Match Accuracy (threshold set to 85 for near matches)
                    fuzzy_similarity = fuzz.ratio(pred.strip(), ref.strip())
                    fuzzy_match_accuracy = 1 if fuzzy_similarity >= 60 else 0
                    fuzzy_match_accuracies.append(fuzzy_match_accuracy)

                    # Semantic Similarity
                    pred_embedding = self.semantic_model.encode(pred)
                    ref_embedding = self.semantic_model.encode(ref)
                    similarity = cosine_similarity([pred_embedding], [ref_embedding])[0][0]
                    semantic_similarities.append(similarity)

                    # METEOR Score (use tokenized inputs)
                    meteor = meteor_score([ref_tokens], pred_tokens)  # Pass tokenized lists
                    meteor_scores.append(meteor)

        avg_loss = total_loss / len(self.eval_dataloader)
        perplexity = math.exp(avg_loss)

        bleu_score = corpus_bleu(references, predictions)

        rouge_1_f1_scores = []
        rouge_2_f1_scores = []
        rouge_l_f1_scores = []
        for pred, ref in zip(decoded_preds, decoded_refs):
            rouge_1 = self.scorer.score(ref, pred)['rouge1']
            rouge_2 = self.scorer.score(ref, pred)['rouge2']
            rouge_l = self.scorer.score(ref, pred)['rougeL']

            rouge_1_f1_scores.append(rouge_1.fmeasure)
            rouge_2_f1_scores.append(rouge_2.fmeasure)
            rouge_l_f1_scores.append(rouge_l.fmeasure)

        avg_token_level_accuracy = np.mean(token_level_accuracies)
        avg_exact_match_accuracy = np.mean(exact_match_accuracies)
        avg_fuzzy_match_accuracy = np.mean(fuzzy_match_accuracies)
        avg_semantic_similarity = np.mean(semantic_similarities)
        avg_meteor = np.mean(meteor_scores)

        avg_rouge_1_f1 = np.mean(rouge_1_f1_scores)
        avg_rouge_2_f1 = np.mean(rouge_2_f1_scores)
        avg_rouge_l_f1 = np.mean(rouge_l_f1_scores)

        df = pd.DataFrame({
            "Training Loss": [avg_loss],
            "ROUGE-1 (F1)": [avg_rouge_1_f1],
            "ROUGE-2 (F1)": [avg_rouge_2_f1],
            "ROUGE-L (F1)": [avg_rouge_l_f1],
            "Corpus BLEU": [bleu_score],
            "Semantic Similarity": [avg_semantic_similarity],
            "METEOR": [avg_meteor],
            "Token-Level Accuracy": [avg_token_level_accuracy],
            "Exact Match Accuracy": [avg_exact_match_accuracy],
            "Fuzzy Match Accuracy": [avg_fuzzy_match_accuracy],
            "Perplexity": [perplexity]
        })

        print(tabulate(df, headers="keys", tablefmt="psql"))

        metrics = {
            "Validation Loss": avg_loss,
            "perplexity": perplexity,
            "bleu": bleu_score,
            "rouge_1_f1": avg_rouge_1_f1,
            "rouge_2_f1": avg_rouge_2_f1,
            "rouge_l_f1": avg_rouge_l_f1,
            "semantic_similarity": avg_semantic_similarity,
            "meteor": avg_meteor,
            "token_level_accuracy": avg_token_level_accuracy,
            "exact_match_accuracy": avg_exact_match_accuracy,
            "fuzzy_match_accuracy": avg_fuzzy_match_accuracy,
        }

        wandb.log(metrics)

        return metrics

    def train_epoch(self):
        ''' To Train for Single Epoch '''
        self.model.train()
        for batch in tqdm(self.train_dataloader, desc="Training"):
            self.optimizer.zero_grad()
            inputs = {key: val.to(self.device) for key, val in batch.items()}
            outputs = self.model(**inputs)
            loss = outputs.loss
            loss.backward()
            self.optimizer.step()
            self.scheduler.step()

            wandb.log({"train_loss": loss.item()})

    def train(self, epochs):
        ''' To Train for N Number of Epochs Passed from User '''
        for epoch in range(epochs):
            print(f'Epoch {epoch+1}/{epochs}')
            self.train_epoch()
            metrics = self.evaluate()
            print(f"Metrics: {metrics}")
            torch.save(self.model.state_dict(), f"model_{epoch}.pth")



In [18]:
def objective(trial):
    learning_rate = trial.suggest_float('learning_rate', 1e-5, 1e-3, log='True')
    weight_decay = trial.suggest_float('weight_decay', 1e-5, 1e-1, log='True')
    dropout = trial.suggest_float('dropout', 0.1, 0.5)
    attention_dropout = trial.suggest_float('attention_dropout', 0.1, 0.5)
    num_beams = trial.suggest_int('num_beams', 1, 10)
    batch_size = trial.suggest_categorical('batch_size', [8, 16, 32])
    warmup_steps = trial.suggest_int('warmup_steps', 0, 1000)

    print(f"Trial parameters: "
          f"learning_rate={learning_rate}, "
          f"weight_decay={weight_decay}, "
          f"dropout={dropout}, "
          f"attention_dropout={attention_dropout}, "
          f"num_beams={num_beams}, "
          f"batch_size={batch_size}, "
          f"warmup_steps={warmup_steps}")


    train_dataloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=False)
    val_dataloader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)

    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    model = BartForConditionalGeneration.from_pretrained('facebook/bart-base').to(device)
    config = {'project_name': 'VQA_BART_Tuning_Final2',
        'epochs': 5,
        'learning_rate': learning_rate,
        'weight_decay': weight_decay,
        'dropout': dropout,
        'attention_dropout': attention_dropout,
        'num_beams': num_beams,
        'warmup_steps': warmup_steps,
        }

    trainer = VQA_Trainer(model, train_dataloader, val_dataloader, device=device, config=config)

    trainer.train(config['epochs'])

    metrics = trainer.evaluate()
    return metrics['fuzzy_match_accuracy']

In [16]:
!pip install optuna_dashboard

/opt/conda/lib/python3.10/pty.py:89: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid, fd = os.forkpty()


In [ ]:
from optuna_dashboard import run_server
import optuna

storage = optuna.storages.InMemoryStorage()
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=20)

[I 2024-12-09 15:49:15,024] A new study created in memory with name: no-name-d2fa36c3-e085-4bca-8616-046f225bc985


Trial parameters: learning_rate=4.367948225751944e-05, weight_decay=0.0004354920859245283, dropout=0.28212633542223053, attention_dropout=0.3672834627176522, num_beams=8, batch_size=32, warmup_steps=482


/opt/conda/lib/python3.10/site-packages/transformers/optimization.py:591: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: loozasubedy998 (looza). Use `wandb login --relogin` to force relogin


Epoch 1/5


Evaluating:   0%|          | 0/23 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Evaluating: 100%|██████████| 23/23 [01:05<00:00,  2.85s/it]


+----+-----------------+----------------+----------------+----------------+---------------+-----------------------+----------+------------------------+------------------------+------------------------+--------------+
|    |   Training Loss |   ROUGE-1 (F1) |   ROUGE-2 (F1) |   ROUGE-L (F1) |   Corpus BLEU |   Semantic Similarity |   METEOR |   Token-Level Accuracy |   Exact Match Accuracy |   Fuzzy Match Accuracy |   Perplexity |
|----+-----------------+----------------+----------------+----------------+---------------+-----------------------+----------+------------------------+------------------------+------------------------+--------------|
|  0 |        0.739824 |       0.309103 |       0.119486 |       0.270771 |     0.0733342 |              0.614062 | 0.224555 |                0.10023 |                      0 |              0.0806676 |      2.09557 |
+----+-----------------+----------------+----------------+----------------+---------------+-----------------------+----------+------

Training:  19%|█▉        | 39/203 [00:14<01:00,  2.71it/s]

In [ ]:
print('Best hyperparameters:', study.best_params)
print('Best Accuracy:', study.best_value)

In [ ]:
import optuna.visualization as vis
from matplotlib import pyplot as plt

fig = vis.plot_optimization_history(study)
fig.show()
plt.savefig("Optimization-history.png")

In [ ]:
fig = vis.plot_parallel_coordinate(study)
fig.show()

plt.savefig('parallel-coordinates.png')


In [ ]:
fig = vis.plot_param_importances(study)
fig.show()

plt.savefig('hyperparameter-importances.png')

In [ ]:
fig = vis.plot_slice(study, params=['learning_rate'])
fig.show()

plt.savefig('learning-rate.png')